# (Optional but recommeded) Set up Virtual Environment

TODO

# 1. Install pipeline dependencies
In order to use the pipeline, you need to install some dependencies the pipeline relies on. Run the following command to install the dependencies defined in requirements.txt

In [ ]:
%pip install -r requirements.txt

# 2. Instantiate pipeline

In [6]:
from transformers import pipeline

rpeak2hrv_pipeline = pipeline(model = "hubii-world/rpeaks-to-hrv-pipeline", trust_remote_code=True)

config.json:   0%|          | 0.00/829 [00:00<?, ?B/s]

rpeaks_2_hrv_pipeline.py:   0%|          | 0.00/1.76k [00:00<?, ?B/s]

rpeaks2hrv.py:   0%|          | 0.00/7.54k [00:00<?, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/hubii-world/rpeaks-to-hrv-pipeline:
- rpeaks2hrv.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
A new version of the following files was downloaded from https://huggingface.co/hubii-world/rpeaks-to-hrv-pipeline:
- rpeaks_2_hrv_pipeline.py
- rpeaks2hrv.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


model.safetensors:   0%|          | 0.00/649k [00:00<?, ?B/s]

Device set to use cpu


# 3. Overview: Pipeline parameters
The pipeline provides a variety of different parameters that can be set to adjust the preprocessing behavior. In the following, the different Parameters are explained and usage examples are provided.


### Mandatory parameters
In general, the pipeline relies on 2 mandatory parameters the user has to set for every parameter execution:
- `inputs` : str | pd.DataFrame - The input that should be processed by the pipeline. This can either be a path to a file containing the data to process or the data itself
- `sampling_rate` : int - The sampling rate of the continuous cardiac signal in which peaks occur. Default value is 1000


### Optional parameters
Besides the mandatory parameter, the pipeline offers multiple optional parameters that may be necessary to set in order to compute correct HRV-features:
- `time_header` : str - The name of the column in the data that contains the timestamp to which the respective values in the same row are recorded. Default setting is 'SystemTime'
- `rri_header` : str - The name of the column in the data that contains the RR-Intervals in msec. Default setting is 'interbeat_interval'
- `windowing_method` : str - The method that should be applied to divide the raw data into windows. Default setting is None, so no windowing is applied
- `window_size` : str - The size of a window in terms of a time frame. Only relevant if windowing should be applied to the data. Default setting is 60 seconds


##  3.1 `Inputs`

The `inputs` parameter represents the data the pipeline should process to HRV-Features. The following input formats are supported:
- str
- pd.Dataframe

When providing the inputs as string, it has to represent a file path to a file containing the data to process. Supported file formats are .csv, .txt.

Alternatively, you can also provide the data directly to the pipeline in form of a DataFrame.

### 3.1.1 Example: Provide input as file path

In [9]:
file_path = "./Data/hr_rr_Elias-Rec_1703_162053.csv"
result = rpeak2hrv_pipeline(inputs=file_path, feature_domains=['time', 'freq'], sampling_rate=1000)
result.head()

HRV_MeanNN    HRV_SDNN  HRV_SDANN1  HRV_SDNNI1  HRV_SDANN2  HRV_SDNNI2  \
0  1006.894005  159.530641   72.830794  137.277955   56.912177    143.4821   

   HRV_SDANN5  HRV_SDNNI5   HRV_RMSSD    HRV_SDSD  ...   HRV_ULF   HRV_VLF  \
0   45.675812  152.633402  107.280546  102.397785  ...  0.000497  0.010289   

     HRV_LF    HRV_HF   HRV_VHF    HRV_TP  HRV_LFHF   HRV_LFn  HRV_HFn  \
0  0.024415  0.070705  0.026376  0.132282  0.345306  0.184566   0.5345   

   HRV_LnHF  
0 -2.649243  

[1 rows x 35 columns]

## 3.2 `sampling_rate`
The sampling_rate (Hz) represents the rate with which the sensor sampled data from the patient. It has to be provided as integer. In the example above, you can see a configuration where the sampling_rate is set to 2000.

The default rate is 1000 Hz, meaning that the sensor sampled 1000 values per second.

## 3.3 `time_header` & `rri_header`
time_header and rri_header are important settings to define the structure of the data the pipeline has to process. In general, the pipeline supports two possible data formats:
- R Peak Flags
- RR-Intervals with timestamps

### 3.3.1 R Peak Flags
The first format option is defined by a Dataframe with one column named `'ECG_R_Peaks'`. The column values are simple binary flags indicating whether a R peak occured or not. 

This is the standard data format used by neurokit to represent R peaks. If you use this data format, you do not need to specify `time_header` and `rri_header`.

__Important__: Make sure that the column has the correct name and that you specify the correct sampling rate, as these are indispensable information to compute the correct HRV-Features.

#### Example: R Peak Flags

TODO

### 3.3.2 RR-Intervals with timestamps
The second format option is defined by a DataFrame with two columns containing the RR-Intervals in milliseconds and the corresponding timestamps at which the RR-intervals have been recorded by the sensor. Here, `time_header` speficies the column name containing the timestamps and `rri_header` speficies the column containing the RR-intervals.
The default column names are `'SystemTime'` and `'interbeat_intervals'`.
#### Example: RR-Intervals with timestamps

TODO

## 3.4 `windowing_method`
The windowing_method defines the method to be used to divide the raw data into windows. The supported settings are:
- 'rolling' - Creates a window rolling over the data. For more information see [pandas.DataFrame.rolling()](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.rolling.html)
- 'first_interval' - Keeps the data values that are recorded within the first timeframe defined by window_size and omits the rest
- 'last_interval'-  Keeps the data values that are recorded within the last timeframe defined by window_size and omits the rest


# 3.4.1 Example: Use 'first_interval'-windowing
The following code snipped shows an exemplary usage of first_interval windowing. In this example, only the values recorded within the first 60s of the data collection are used to compute HRV-Features

In [4]:
file_path = "./Data/hr_rr_Elias-Rec_1703_162053.csv"
result = rpeak2hrv_pipeline(inputs=file_path, windowing_method="first_interval", window_size="60s", sampling_rate=1000)
result.head()

c:\Users\georg\Desktop\HIWI\ECG2HRV\.venv\Lib\site-packages\neurokit2\hrv\hrv_nonlinear.py:268: NeuroKitWarning: Missing interbeat intervals have been detected. Note that missing intervals can distort some HRV features, in particular nonlinear indices.
  warn(
c:\Users\georg\Desktop\HIWI\ECG2HRV\.venv\Lib\site-packages\neurokit2\hrv\hrv_nonlinear.py:529: NeuroKitWarning: DFA_alpha2 related indices will not be calculated. The maximum duration of the windows provided for the long-term correlation is smaller than the minimum duration of windows. Refer to the `scale` argument in `nk.fractal_dfa()` for more information.
  warn(
C:\Users\georg\.cache\huggingface\modules\transformers_modules\willergeorg\rpeaks-to-hrv-pipeline\354dfd60f24b9b5900052952ca632b87456e4701\rpeaks2hrv.py:24: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To r

window_start                    window_end   HRV_MeanNN  \
0 2025-03-17 16:20:54.760848 2025-03-17 16:21:53.596623680  1060.358416   

     HRV_SDNN  HRV_SDANN1  HRV_SDNNI1  HRV_SDANN2  HRV_SDNNI2  HRV_SDANN5  \
0  153.515505         NaN         NaN         NaN         NaN         NaN   

   HRV_SDNNI5  ...  HRV_SampEn  HRV_ShanEn  HRV_FuzzyEn  HRV_MSEn  HRV_CMSEn  \
0         NaN  ...    1.265666    5.657451     1.330316  0.856145     0.9913   

   HRV_RCMSEn   HRV_CD   HRV_HFD   HRV_KFD   HRV_LZC  
0    1.267671  1.82538  2.016523  2.937446  1.227977  

[1 rows x 84 columns]

## 3.5 `window_size`
The window_size defines the size of the windows the data should be divided in. In general, the definition follows this pattern: '{any positive integer}{t}', where t is an element of {'d', 'h', 'm', 's'}.

For example: the setting '20m' represents a window size of 20 minutes.

The default setting is '60s' corresponding to a window size of a minute.

Setting this parameter is only necessary, if you want to apply windowing.

### Example: Window size

TODO

# 4. Supported file formats

TODO